In [1]:
import numpy as np
import pandas as pd
from astropy.time import Time
import h5py
from pycbc.conversions import mchirp_from_mass1_mass2,primary_mass,secondary_mass,chi_eff
import pylab,os,shutil
import matplotlib.pyplot as plt
pd.set_option('display.max_columns',None)

# Select those interesting triggers

In [2]:
fourogc = h5py.File('/work/ahnitz/WWW/4ogc/4-ogc.hdf')

In [5]:
Time(fourogc['time'][i],format='gps').datetime64

array(['2019-07-01T22:33:32.652099609'], dtype='datetime64[ns]')

In [6]:
gwfile = fourogc

# convert the GW events name to UTF-8 format
gwobs = np.array([obs.decode("utf-8") for obs in gwfile['trig'][:]])

mass1 = np.array(gwfile['mass1'])
mass2 = np.array(gwfile['mass2'])
stat = np.array(gwfile['stat'])
spin1z = np.array(gwfile['spin1z'])
spin2z = np.array(gwfile['spin2z'])
spin = chi_eff(gwfile['mass1'][:], gwfile['mass2'][:],gwfile['spin1z'][:], gwfile['spin2z'][:])
name_gw = np.array(gwfile['name'])
ifar = np.array(gwfile['ifar'])
time_gw = np.array(gwfile['time'])

In [7]:
lmass = (mass2<=2) & (mass1<=2)
lspin = (spin<0.2) & (spin>-0.2)

#at least two detectors
# This doesn't affect the results because single detector trigger doesn't have a IFAR
ltrig = (gwobs == 'HL') | (gwobs == 'HLV') | (gwobs == 'LV') | (gwobs == 'HV')

#false alarm rate < every 10 min
yr2min = 365.25*24*60
lifar = (gwfile['ifar'][:] > 1/yr2min * 1)
lifar = True
#ltrig = True

# time during O3a start and 2019 07, 02 00:00:00
ltime = (gwfile['time'][:] > Time('2019-04-01T00:00:00').gps) & (gwfile['time'][:] < Time('2019-07-02T00:00:00').gps)
l = lmass & lspin & ltrig & lifar & ltime
print('There are ', l.sum(), ' triggers')

# the index of a qualified GW event
gwidx = np.where(l)[0]

There are  294489  triggers


In [8]:
gwobs = gwobs[gwidx]
mass1 = mass1[gwidx]
mass2 = mass2[gwidx]
spin1z = spin1z[gwidx]
spin2z = spin2z[gwidx]
name_gw = name_gw[gwidx]
ifar = ifar[gwidx]
time_gw = time_gw[gwidx]
stat = stat[gwidx]

In [9]:
len(time_gw)

294489

In [10]:
len(stat)

294489

In [11]:
np.where(time_gw[1:]-time_gw[:-1]<=0)

(array([], dtype=int64),)

# FRB

In [12]:
#FRB file: CHIME FRB catalog 1
frb = pd.read_csv('/work/yifan.wang/em/gitrepo/chimefrbcat1.csv')
# convert the mjd_inf time to a datetime64 format
frb_t =  Time(frb['mjd_inf'][:],format='mjd').datetime64

tO3_start = Time('2019-04-01T00:00:00')
tO3_end = Time('2019-07-02T00:00:00')

frb = frb[(frb_t <tO3_end) & (frb_t > tO3_start) & (frb['repeater_name'] == '-9999')] #not a repeated FRB

In [13]:
#add a new column called 'gpstime'
frb['gpstime'] = Time(frb['mjd_inf'][:],format='mjd').gps

#make four arrays which will be useful
t_frb = np.array(frb['gpstime'])
name_frb = np.array(frb['tns_name'])
ra_frb = np.array(frb['ra'])/ 180 * np.pi
dec_frb = np.array(frb['dec']) / 180 * np.pi

# There are 151 FRB events

In [14]:
name_frb, uid = np.unique(name_frb, return_index=True)
ra_frb = ra_frb[uid]
dec_frb = dec_frb[uid]
t_frb = t_frb[uid]

In [15]:
uid

array([  0,   1,   3,   4,   5,   6,   7,   8,   2,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  39,  38,
        40,  41,  43,  42,  46,  48,  50,  51,  52,  53,  54,  55,  56,
        57,  58,  59,  61,  60,  62,  63,  65,  66,  67,  68,  69,  70,
        71,  73,  72,  74,  75,  76,  77,  78,  79,  80,  81,  82,  83,
        84,  85,  87,  88,  89,  90,  91,  92,  93,  94,  95,  97,  96,
        99, 102, 100, 101, 103, 104, 105, 106, 107, 108, 109, 110, 112,
       113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125,
       126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138,
       139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151,
       152, 153, 154, 155, 156, 157, 158, 159])

In [16]:
len(ra_frb)

151

In [17]:
np.where(name_frb=='FRB20190425A')

(array([48]),)

In [18]:
name_frb[48:]

array(['FRB20190425A', 'FRB20190425B', 'FRB20190426A', 'FRB20190427A',
       'FRB20190428A', 'FRB20190429A', 'FRB20190429B', 'FRB20190430A',
       'FRB20190430B', 'FRB20190430C', 'FRB20190501B', 'FRB20190502A',
       'FRB20190502B', 'FRB20190502C', 'FRB20190515A', 'FRB20190515B',
       'FRB20190515D', 'FRB20190516B', 'FRB20190517C', 'FRB20190517D',
       'FRB20190518B', 'FRB20190518C', 'FRB20190518D', 'FRB20190518G',
       'FRB20190519D', 'FRB20190519E', 'FRB20190519F', 'FRB20190519G',
       'FRB20190519H', 'FRB20190519J', 'FRB20190520A', 'FRB20190527A',
       'FRB20190527C', 'FRB20190529A', 'FRB20190530A', 'FRB20190531A',
       'FRB20190531B', 'FRB20190531C', 'FRB20190531E', 'FRB20190601A',
       'FRB20190601B', 'FRB20190601C', 'FRB20190601D', 'FRB20190603B',
       'FRB20190604C', 'FRB20190604D', 'FRB20190604E', 'FRB20190604G',
       'FRB20190605C', 'FRB20190605D', 'FRB20190606B', 'FRB20190607A',
       'FRB20190607B', 'FRB20190608A', 'FRB20190609A', 'FRB20190609B',
      

In [19]:
t_frb[48:]

array([1.24022449e+09, 1.24025074e+09, 1.24027730e+09, 1.24044088e+09,
       1.24046288e+09, 1.24057507e+09, 1.24058722e+09, 1.24065665e+09,
       1.24065120e+09, 1.24066044e+09, 1.24074323e+09, 1.24080621e+09,
       1.24081744e+09, 1.24084778e+09, 1.24196087e+09, 1.24197294e+09,
       1.24198910e+09, 1.24201307e+09, 1.24216601e+09, 1.24214033e+09,
       1.24218717e+09, 1.24220299e+09, 1.24220549e+09, 1.24225445e+09,
       1.24227072e+09, 1.24227173e+09, 1.24227181e+09, 1.24230530e+09,
       1.24231522e+09, 1.24234225e+09, 1.24238311e+09, 1.24300969e+09,
       1.24303099e+09, 1.24319556e+09, 1.24328207e+09, 1.24331487e+09,
       1.24332768e+09, 1.24334480e+09, 1.24335530e+09, 1.24339710e+09,
       1.24344190e+09, 1.24345883e+09, 1.24345772e+09, 1.24357832e+09,
       1.24371467e+09, 1.24365789e+09, 1.24366654e+09, 1.24372516e+09,
       1.24373646e+09, 1.24378876e+09, 1.24389479e+09, 1.24396078e+09,
       1.24396453e+09, 1.24404079e+09, 1.24408357e+09, 1.24413407e+09,
      

In [20]:
t_frb[1:]-t_frb[:-1]

array([ 8.12104504e+04,  7.00596762e+04,  6.14908282e+03,  2.69183250e+04,
        2.03589729e+04,  1.36287167e+04,  3.12577088e+03, -7.70885840e+04,
        1.00702173e+05,  2.82918004e+04,  1.04532452e+05,  2.14043358e+04,
        2.19268491e+05,  4.22240306e+04,  1.17803925e+04,  2.98698669e+04,
        2.01078047e+04,  6.84711867e+04,  4.74284420e+02,  4.37725683e+04,
        1.58078925e+04,  5.15940797e+04,  5.60186782e+04,  1.01579550e+04,
        1.47296412e+05,  1.58672063e+04,  7.03758395e+04,  4.48209017e+04,
        1.56419265e+04,  1.69805761e+04,  6.19806406e+03,  8.71186120e+04,
        5.52198561e+04,  9.07258975e+04,  9.72165457e+03,  7.69311534e+04,
        9.37099822e+03, -2.81301998e+03,  3.67645527e+04,  1.32428454e+05,
        7.83378484e+04, -6.01817639e+04,  9.17618566e+04,  2.83307256e+04,
        1.34622757e+04,  9.24345849e+03,  3.20645436e+04,  1.06995626e+05,
        2.62509015e+04,  2.65559644e+04,  1.63581619e+05,  2.20052814e+04,
        1.12189504e+05,  

In [21]:
sortidx = np.argsort(t_frb)

In [22]:
sortidx

array([  0,   1,   8,   2,   3,   4,   5,   6,   7,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  38,  37,
        39,  40,  42,  41,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  56,  55,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  67,  66,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  90,  89,
        91,  93,  94,  92,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142,
       143, 144, 145, 146, 147, 148, 149, 150])

In [23]:
t_frb = t_frb[sortidx]
ra_frb = ra_frb[sortidx]
dec_frb = dec_frb[sortidx]
name_frb = name_frb[sortidx]

In [24]:
Time(t_frb[np.where(name_frb=='FRB20190425A')],format='gps').datetime64

array(['2019-04-25T10:48:27.612394810'], dtype='datetime64[ns]')

In [25]:
for n in name_frb:
    print(n,Time(t_frb[np.where(name_frb==n)],format='gps').datetime64)

FRB20190401A ['2019-04-01T08:36:43.554188728']
FRB20190402A ['2019-04-02T07:10:14.004630089']
FRB20190403G ['2019-04-03T00:42:45.964979172']
FRB20190403A ['2019-04-03T02:37:53.680835009']
FRB20190403B ['2019-04-03T04:20:22.763651609']
FRB20190403C ['2019-04-03T11:49:01.088608027']
FRB20190403D ['2019-04-03T17:28:20.061472178']
FRB20190403E ['2019-04-03T21:15:28.778144360']
FRB20190403F ['2019-04-03T22:07:34.549023628']
FRB20190404A ['2019-04-04T04:41:08.138349056']
FRB20190404B ['2019-04-04T12:32:39.938773394']
FRB20190405A ['2019-04-05T17:34:52.390566587']
FRB20190405B ['2019-04-05T23:31:36.726361752']
FRB20190408A ['2019-04-08T12:26:05.217539310']
FRB20190409A ['2019-04-09T00:09:49.248150587']
FRB20190409B ['2019-04-09T03:26:09.640700579']
FRB20190409C ['2019-04-09T11:43:59.507593632']
FRB20190409D ['2019-04-09T17:19:07.312287807']
FRB20190410A ['2019-04-10T12:20:18.499004841']
FRB20190410B ['2019-04-10T12:28:12.783424377']
FRB20190411A ['2019-04-11T00:37:45.351679325']
FRB20190411B 

In [26]:
ra_frb[-1],dec_frb[-1]

(2.418502744488542, 1.0770426814057008)

In [27]:
frb[frb['tns_name']=='FRB20190701E']['ra'] / 180 * np.pi

599    2.418503
Name: ra, dtype: float64

In [28]:
frb[frb['tns_name']=='FRB20190701E']['dec'] / 180 * np.pi

599    1.077043
Name: dec, dtype: float64

In [29]:
np.where(t_frb[1:]-t_frb[:-1]<=0)

(array([], dtype=int64),)

# Make triggers: Time window [-100,100]

In [30]:
#[t_frb ---600s--- t_gw ----------- 3600s ------------- t_frb]
left = np.searchsorted(t_frb,  time_gw- 100)
right = np.searchsorted(t_frb, time_gw + 100)

# The index of 'left' is GW index, the value of 'left' is frb index
gw_co_idx = np.where((right - left) > 0)[0]
frb_co_idx = left[gw_co_idx]
print('There are ', len(gw_co_idx), 'coincidence.')

There are  1050 coincidence.


In [31]:
left

array([  1,   1,   1, ..., 151, 151, 151])

In [32]:
len(left)

294489

In [33]:
for n in gw_co_idx:
    print(name_gw[n],Time(time_gw[n],format='gps').datetime64,mass1[n],mass2[n])

b'190403_023537' 2019-04-03T02:36:14.228759766 1.1768218056648743 1.032298631645515
b'190403_023559' 2019-04-03T02:36:36.370361328 1.434660263451193 1.6251487967038813
b'190403_023610' 2019-04-03T02:36:47.379638672 1.6271080385797014 1.7758733682551862
b'190403_023639' 2019-04-03T02:37:16.632568359 1.0669656464359942 1.4098445024800907
b'190403_023702' 2019-04-03T02:37:39.951904297 1.1069465758723345 1.0521759998174491
b'190403_023746' 2019-04-03T02:38:23.626220703 1.3185591071943006 1.3589097399046839
b'190403_023816' 2019-04-03T02:38:53.232421875 1.8610107053752478 1.7318110698209905
b'190403_023841' 2019-04-03T02:39:18.518066406 1.128465358921908 1.1122641066239025
b'190403_041823' 2019-04-03T04:19:00.518554688 1.2330514861366302 1.1567299871278867
b'190403_041850' 2019-04-03T04:19:27.323730469 1.129668911364055 1.9369695848794322
b'190403_041914' 2019-04-03T04:19:51.550781250 1.2981391441025174 1.2105290950676992
b'190403_041927' 2019-04-03T04:20:04.397949219 1.6764627198478972 1.5

b'190420_002610' 2019-04-20T00:26:47.199218750 1.0386113951119837 1.5111629680436436
b'190420_002641' 2019-04-20T00:27:18.027587891 1.0013007283276707 1.0002535307655467
b'190420_002701' 2019-04-20T00:27:38.394287109 1.5354145577229958 1.919660496796716
b'190420_002722' 2019-04-20T00:27:59.851562500 1.2185708555745436 1.0530377097883155
b'190420_002747' 2019-04-20T00:28:24.414062500 1.0000134800600007 1.000524462194278
b'190420_002803' 2019-04-20T00:28:40.990478516 1.5693828553423435 1.0485080251713994
b'190420_002834' 2019-04-20T00:29:11.181884766 1.0600493958455033 1.066517726843204
b'190420_002909' 2019-04-20T00:29:46.980712891 1.539201197636976 1.0504941049854484
b'190420_011256' 2019-04-20T01:13:33.430419922 1.2253389441758245 1.0232601013444609
b'190420_011313' 2019-04-20T01:13:50.850830078 1.0572100275412706 1.1226541856099281
b'190420_011337' 2019-04-20T01:14:14.215087891 1.9613220791785244 1.886342516611361
b'190420_011351' 2019-04-20T01:14:28.501953125 1.3334477747797215 1.38

b'190517_220510' 2019-05-17T22:05:47.117431641 1.1007359338312512 1.3673092298272875
b'190517_220549' 2019-05-17T22:06:26.917480469 1.7287421525960205 1.9043464634016856
b'190517_220601' 2019-05-17T22:06:38.722167969 1.4766239040990956 1.683626944708288
b'190517_220633' 2019-05-17T22:07:10.979248047 1.1150643304752343 1.5452871585597463
b'190517_220646' 2019-05-17T22:07:23.135986328 1.185297478950658 1.0342447506039285
b'190517_220705' 2019-05-17T22:07:42.946289063 1.2523305296990344 1.8541612646550756
b'190517_220738' 2019-05-17T22:08:15.154541016 1.0597171413820574 1.0922071977173622
b'190517_220751' 2019-05-17T22:08:28.107666016 1.7963187217415657 1.0107965362751428
b'190517_220810' 2019-05-17T22:08:47.371093750 1.2409286531333508 1.1653526313806766
b'190518_082147' 2019-05-18T08:22:24.323486328 1.0538146584449573 1.041728177693677
b'190518_082226' 2019-05-18T08:23:03.884033203 1.560270407884118 1.0998859498520677
b'190518_082245' 2019-05-18T08:23:22.515625000 1.325953186152288 1.27

b'190603_062349' 2019-06-03T06:24:26.160888672 1.9662855179433243 1.2276399197196217
b'190603_062403' 2019-06-03T06:24:40.376708984 1.3868702560770285 1.3629741177387904
b'190603_062447' 2019-06-03T06:25:24.551513672 1.3415405220246006 1.352970807929833
b'190603_062513' 2019-06-03T06:25:50.845214844 1.4326428871194876 1.0284824374893082
b'190603_062555' 2019-06-03T06:26:32.457519531 1.011837487352471 1.9212264606035907
b'190603_062617' 2019-06-03T06:26:54.146972656 1.0032646378065173 1.0001284204720364
b'190604_042940' 2019-06-04T04:30:17.194580078 1.71727811414423 1.1623480421910715
b'190604_043014' 2019-06-04T04:30:51.348144531 1.9370239316219817 1.1606208996053824
b'190604_043040' 2019-06-04T04:31:17.708496094 1.0283685009809256 1.1146983467410694
b'190604_043104' 2019-06-04T04:31:41.942382813 1.0486659485416558 1.1025565296225854
b'190604_043127' 2019-06-04T04:32:04.273681641 1.8734287529262568 1.6959090796769365
b'190604_043145' 2019-06-04T04:32:22.165527344 1.17023674020904 1.002

b'190616_055706' 2019-06-16T05:57:43.131103516 1.6442170115824604 1.3243729624184235
b'190616_055730' 2019-06-16T05:58:07.237548828 1.204715617360725 1.2414717008228713
b'190616_055749' 2019-06-16T05:58:26.942382813 1.4193760071624593 1.3654863879010122
b'190616_055808' 2019-06-16T05:58:45.595458984 1.4929263629999605 1.280172655906818
b'190617_021059' 2019-06-17T02:11:36.374267578 1.0823976188816284 1.0676632792755134
b'190617_021137' 2019-06-17T02:12:14.188720703 1.1452839486930593 1.054911596909643
b'190617_021148' 2019-06-17T02:12:25.726806641 1.0076782051700808 1.0016757368704807
b'190617_021213' 2019-06-17T02:12:50.775878906 1.42780865486367 1.8004990339571125
b'190617_021229' 2019-06-17T02:13:06.573242187 1.3058556888863215 1.0982118426462053
b'190617_021245' 2019-06-17T02:13:22.261230469 1.5615596879977576 1.6423829822377916
b'190617_021312' 2019-06-17T02:13:49.730224609 1.1500547344625367 1.1338799809893065
b'190617_021327' 2019-06-17T02:14:04.117431641 1.2158160670750562 1.09

b'190629_135429' 2019-06-29T13:55:06.315185547 1.9831556801998966 1.5890892665318777
b'190629_135454' 2019-06-29T13:55:31.556640625 1.1488351120123403 1.7089818965294143
b'190630_111722' 2019-06-30T11:17:59.283691406 1.073777491451453 1.0645290734284174
b'190630_111745' 2019-06-30T11:18:22.097656250 1.8251190179964714 1.140176907855571
b'190630_111757' 2019-06-30T11:18:34.277832031 1.5516689984496583 1.4240890499360133
b'190630_111829' 2019-06-30T11:19:06.579833984 1.1523803485894062 1.3967177587016386
b'190630_111854' 2019-06-30T11:19:31.142333984 1.6125007358719972 1.7889907525220188
b'190630_111917' 2019-06-30T11:19:54.265136719 1.2812959988372192 1.1475955475638582
b'190630_111939' 2019-06-30T11:20:16.279296875 1.062267882726923 1.9809164583461027
b'190630_111955' 2019-06-30T11:20:32.962890625 1.0175305309161318 1.6198991237982157
b'190630_112013' 2019-06-30T11:20:50.117431641 1.0978968740209518 1.0048244128546813
b'190630_112030' 2019-06-30T11:21:07.460449219 1.0092646155854519 1.

In [34]:
gw_co_idx

array([  3708,   3709,   3710, ..., 294238, 294239, 294240])

In [35]:
len(gw_co_idx)

1050

# Make background: Time window [-100,100]

# Make another file and just store all the chunk name and stat in  

In [36]:
mass1

array([1.73028057, 1.55424614, 1.06256066, ..., 1.16727983, 1.9411788 ,
       1.06221527])

In [37]:
len(mass1)

294489

In [38]:
n = 100
step = (tO3_end.gps - tO3_start.gps) / (n+1)

chunkname = []
saveresult = []
savename = []

for nvalue in range(n):
    print('chunk:',nvalue)
    
    offset = (nvalue + 1) * step
    t_frb_timeslide = (t_frb + offset) % tO3_end.gps + (t_frb+offset)//tO3_end.gps * tO3_start.gps
    
    # sort the t_frb
    sortfrb = np.argsort(t_frb_timeslide)
    t_frb_timeslide = t_frb_timeslide[sortfrb]
    ra_timeslide = ra_frb[sortfrb]
    dec_timeslide = dec_frb[sortfrb]
    #[t_frb ---100s--- t_gw ----------- 100s ------------- t_frb]
    left = np.searchsorted(t_frb_timeslide, time_gw - 100)
    right = np.searchsorted(t_frb_timeslide, time_gw + 100)

    gw_co_idx = np.where((right - left) > 0)[0]
    frb_co_idx = left[gw_co_idx]
    print('There are ', len(gw_co_idx), 'coincidence.')

    itrig = 0

    for ii,vv in enumerate(gw_co_idx):
        chunkname.append('chunk'+str(nvalue)+'_'+str(itrig))
        saveresult.append(stat[vv])
        savename.append(name_gw[vv])
        itrig  +=1

chunk: 0
There are  1086 coincidence.
chunk: 1
There are  1125 coincidence.
chunk: 2
There are  1085 coincidence.
chunk: 3
There are  1165 coincidence.
chunk: 4
There are  1223 coincidence.
chunk: 5
There are  1032 coincidence.
chunk: 6
There are  1086 coincidence.
chunk: 7
There are  1183 coincidence.
chunk: 8
There are  1102 coincidence.
chunk: 9
There are  1097 coincidence.
chunk: 10
There are  1157 coincidence.
chunk: 11
There are  1059 coincidence.
chunk: 12
There are  1174 coincidence.
chunk: 13
There are  1007 coincidence.
chunk: 14
There are  1107 coincidence.
chunk: 15
There are  971 coincidence.
chunk: 16
There are  1025 coincidence.
chunk: 17
There are  1166 coincidence.
chunk: 18
There are  1146 coincidence.
chunk: 19
There are  1131 coincidence.
chunk: 20
There are  1033 coincidence.
chunk: 21
There are  1109 coincidence.
chunk: 22
There are  1141 coincidence.
chunk: 23
There are  1183 coincidence.
chunk: 24
There are  1128 coincidence.
chunk: 25
There are  1123 coincidenc

In [39]:
chunkname

['chunk0_0',
 'chunk0_1',
 'chunk0_2',
 'chunk0_3',
 'chunk0_4',
 'chunk0_5',
 'chunk0_6',
 'chunk0_7',
 'chunk0_8',
 'chunk0_9',
 'chunk0_10',
 'chunk0_11',
 'chunk0_12',
 'chunk0_13',
 'chunk0_14',
 'chunk0_15',
 'chunk0_16',
 'chunk0_17',
 'chunk0_18',
 'chunk0_19',
 'chunk0_20',
 'chunk0_21',
 'chunk0_22',
 'chunk0_23',
 'chunk0_24',
 'chunk0_25',
 'chunk0_26',
 'chunk0_27',
 'chunk0_28',
 'chunk0_29',
 'chunk0_30',
 'chunk0_31',
 'chunk0_32',
 'chunk0_33',
 'chunk0_34',
 'chunk0_35',
 'chunk0_36',
 'chunk0_37',
 'chunk0_38',
 'chunk0_39',
 'chunk0_40',
 'chunk0_41',
 'chunk0_42',
 'chunk0_43',
 'chunk0_44',
 'chunk0_45',
 'chunk0_46',
 'chunk0_47',
 'chunk0_48',
 'chunk0_49',
 'chunk0_50',
 'chunk0_51',
 'chunk0_52',
 'chunk0_53',
 'chunk0_54',
 'chunk0_55',
 'chunk0_56',
 'chunk0_57',
 'chunk0_58',
 'chunk0_59',
 'chunk0_60',
 'chunk0_61',
 'chunk0_62',
 'chunk0_63',
 'chunk0_64',
 'chunk0_65',
 'chunk0_66',
 'chunk0_67',
 'chunk0_68',
 'chunk0_69',
 'chunk0_70',
 'chunk0_71',
 '

In [40]:
saveresult

[-4.231072902679443,
 -2.8420331478118896,
 -5.468386650085449,
 -6.773550987243652,
 1.186706781387329,
 -5.354623794555664,
 -4.043008327484131,
 -9.899121284484863,
 -7.9453535079956055,
 -2.100276231765747,
 -12.076692581176758,
 -8.783214569091797,
 1.1804749965667725,
 5.530562400817871,
 -2.742088794708252,
 -4.264779567718506,
 0.6995333433151245,
 -1.8955132961273193,
 1.145477294921875,
 -0.7775693535804749,
 -7.171664237976074,
 -0.48299843072891235,
 -2.7761802673339844,
 -2.067521095275879,
 -1.7953341007232666,
 -1.1640090942382812,
 -0.8676877021789551,
 -4.625873565673828,
 -10.262404441833496,
 -1.824706792831421,
 -0.5265086889266968,
 -0.48371899127960205,
 -3.6482012271881104,
 3.139181137084961,
 7.1654582023620605,
 -9.053979873657227,
 0.1257230043411255,
 -2.946948528289795,
 -2.759720802307129,
 -2.8613054752349854,
 -3.1904280185699463,
 -6.866176605224609,
 -2.925567388534546,
 -5.410418510437012,
 -3.1630563735961914,
 -4.201547622680664,
 -2.72560453414917,

In [41]:
savename

[b'190401_172701',
 b'190401_172721',
 b'190401_172742',
 b'190401_172755',
 b'190401_172813',
 b'190401_172835',
 b'190401_172853',
 b'190401_172908',
 b'190401_172928',
 b'190401_172952',
 b'190401_184358',
 b'190401_184415',
 b'190401_184433',
 b'190401_184509',
 b'190401_184526',
 b'190401_184540',
 b'190401_184613',
 b'190401_184646',
 b'190401_202157',
 b'190401_202221',
 b'190401_202232',
 b'190401_202249',
 b'190401_202330',
 b'190401_202340',
 b'190401_202409',
 b'190401_202421',
 b'190401_202437',
 b'190401_202448',
 b'190403_045945',
 b'190403_045958',
 b'190403_050016',
 b'190403_050027',
 b'190403_050046',
 b'190403_050104',
 b'190403_050120',
 b'190403_050140',
 b'190403_050208',
 b'190403_050223',
 b'190403_050244',
 b'190403_223215',
 b'190403_223249',
 b'190403_223309',
 b'190403_223328',
 b'190403_223416',
 b'190403_223434',
 b'190403_223445',
 b'190403_223505',
 b'190403_223517',
 b'190404_002725',
 b'190404_002748',
 b'190404_002806',
 b'190404_002818',
 b'190404_00

In [42]:
csvdict = {'chunkname': chunkname,
            'gwname': savename,
            'stat': saveresult,
          }

df = pd.DataFrame(csvdict)

In [43]:
len(df)

111376

In [44]:
df.to_csv('chunksame.csv')

In [45]:
def printgw(name,fourogc=fourogc):
    for key in fourogc.keys():
        print(key, fourogc[key][np.where(fourogc['name'][:]==name.encode())])

In [46]:
printgw('190525_224359')

H1_chisq [-1.]
H1_end_time [-1.]
H1_sg_chisq [-1.]
H1_snr [-1.]
L1_chisq [0.]
L1_end_time [1.24285946e+09]
L1_sg_chisq [1.]
L1_snr [5.14959526]
V1_chisq [-0.]
V1_end_time [1.24285946e+09]
V1_sg_chisq [1.]
V1_snr [4.58143091]
ifar [1.03862595e-07]
mass1 [1.76249261]
mass2 [1.11854055]
name [b'190525_224359']
obs [b'HLV']
pastro [-1.]
spin1z [-0.00418756]
spin2z [0.02412539]
stat [-5.48986197]
time [1.24285946e+09]
trig [b'LV']


In [47]:
printgw('190501_131731')

H1_chisq [-1.]
H1_end_time [-1.]
H1_sg_chisq [-1.]
H1_snr [-1.]
L1_chisq [0.]
L1_end_time [1.24075187e+09]
L1_sg_chisq [1.]
L1_snr [5.21350098]
V1_chisq [-0.]
V1_end_time [1.24075187e+09]
V1_sg_chisq [1.]
V1_snr [5.02287245]
ifar [2.35484994e-07]
mass1 [1.012458]
mass2 [1.29578124]
name [b'190501_131731']
obs [b'HLV']
pastro [-1.]
spin1z [-0.03093438]
spin2z [-0.04637806]
stat [-2.8722558]
time [1.24075187e+09]
trig [b'LV']
